In [4]:
# importing the datasets

import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import string
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, Dense, Flatten, Dropout
from tensorflow.keras.utils import to_categorical




In [5]:
# importing the datasets
bidendata = pd.read_csv('US Election 2020 Tweets/hashtag_joebiden.csv')
trumpdata = pd.read_csv('US Election 2020 Tweets/hashtag_donaldtrump.csv', error_bad_lines=False, engine='python')
trainingdata = pd.read_csv('training data/twitter_sentiment_training_data.csv')


/var/folders/x9/7trw1hcj47vbr9_c1w7dqnvw0000gn/T/ipykernel_43558/2346756719.py:2: DtypeWarning: Columns (1,2,3,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20) have mixed types. Specify dtype option on import or set low_memory=False.
  bidendata = pd.read_csv('US Election 2020 Tweets/hashtag_joebiden.csv')


ParserError: Error tokenizing data. C error: Buffer overflow caught - possible malformed input file.


In [ ]:
# Cleaning

# remove missing values
trainingdata = trainingdata.dropna()

# change sentiment to 0, 1, 2
trainingdata['category'] = trainingdata['category'].replace(1, 2)
trainingdata['category'] = trainingdata['category'].replace(0, 1)
trainingdata['category'] = trainingdata['category'].replace(-1, 0)

## remove rows with no tweet text
bidendata = bidendata.dropna(subset=['tweet'])
trumpdata = trumpdata.dropna(subset=['tweet'])

## removing rows not in the US
bidendata = bidendata[bidendata['country'] == 'United States of America']
trumpdata = trumpdata[trumpdata['country'] == 'United States of America']

## removing rows with missing state
bidendata = bidendata.dropna(subset=['state'])
trumpdata = trumpdata.dropna(subset=['state'])

## remvoing non-string rows
bidendata = bidendata[bidendata['tweet'].apply(lambda x: isinstance(x, str))]
trumpdata = trumpdata[trumpdata['tweet'].apply(lambda x: isinstance(x, str))]
trainingdata = trainingdata[trainingdata['clean_text'].apply(lambda x: isinstance(x, str))]

In [ ]:
# training data categories should have the same amount of tweets
def sample_min_group_size(group):
    return group.sample(trainingdata['category'].value_counts().min()).reset_index(drop=True)

trainingdata = trainingdata.groupby('category').apply(sample_min_group_size)

/var/folders/d_/2b70_n_x1y96wpybwyzvy9km0000gp/T/ipykernel_82613/1185353498.py:5: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  trainingdata = trainingdata.groupby('category').apply(sample_min_group_size)


In [ ]:
# how many are left
print('Biden:', len(bidendata))
print('Trump:', len(trumpdata))

Biden: 153579
Trump: 178885


In [ ]:
# preprocessing the training data
def preprocess(text):
    text = text.lower()
    text = text.translate(str.maketrans('', '', string.punctuation))
    text = text.strip()
    return text

bidendata['tweet'] = bidendata['tweet'].apply(preprocess)
trumpdata['tweet'] = trumpdata['tweet'].apply(preprocess)
trainingdata['clean_text'] = trainingdata['clean_text'].apply(preprocess)

# Training the clasifier

In [ ]:
# Parameters
max_words = 10000 
max_len = 100   

# Tokenizer
tokenizer = Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(trainingdata['clean_text'])

# Tokenize and pad sequences
sequences = tokenizer.texts_to_sequences(trainingdata['clean_text'])
X = pad_sequences(sequences, maxlen=max_len, padding='post')

# One-hot encode labels for multi-class classification
y = to_categorical(trainingdata['category'], num_classes=3)  # 3 classes (-1, 0, 1)


In [ ]:
# Split into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Check the shapes
print(f"X_train shape: {X_train.shape}, y_train shape: {y_train.shape}")
print(f"X_test shape: {X_test.shape}, y_test shape: {y_test.shape}")


X_train shape: (85221, 100), y_train shape: (85221, 3)
X_test shape: (21306, 100), y_test shape: (21306, 3)


In [ ]:
# Define the model
model = Sequential([
    Embedding(input_dim=max_words, output_dim=128, input_length=max_len),
    Flatten(),
    Dense(128, activation='relu'),
    Dropout(0.5), 
    Dense(3, activation='softmax')  # Output layer for 3 classes (0, 1, 2)
])

# Compile the model
model.compile(optimizer='adam',
              loss='categorical_crossentropy',
              metrics=['accuracy'])



In [ ]:
# Train the model
history = model.fit(
    X_train, y_train,
    validation_split=0.2,
    epochs=3,
    batch_size=16
)

Epoch 1/3
4261/4261 [==============================] - 26s 6ms/step - loss: 0.4682 - accuracy: 0.8191 - val_loss: 0.2742 - val_accuracy: 0.9122
Epoch 2/3
4261/4261 [==============================] - 25s 6ms/step - loss: 0.1975 - accuracy: 0.9403 - val_loss: 0.2696 - val_accuracy: 0.9187
Epoch 3/3
4261/4261 [==============================] - 23s 5ms/step - loss: 0.1062 - accuracy: 0.9654 - val_loss: 0.3215 - val_accuracy: 0.9162


In [ ]:
# the 6 categories
positive_trump = []
negative_trump = []
neutral_trump = []

positive_biden = []
negative_biden = []
neutral_biden = []

In [ ]:
# processing the biden and trump text
def preprocess_tweets(texts, max_len=100):
    # Convert texts to sequences
    sequences = tokenizer.texts_to_sequences(texts)
    # Pad sequences
    padded_sequences = pad_sequences(sequences, maxlen=max_len, padding='post')
    return padded_sequences



preprocessed_tweets_trump = preprocess_tweets(trumpdata['tweet'])
preprocessed_tweets_biden = preprocess_tweets(bidendata['tweet'])

In [4]:
# Predict probabilities
trump_predictions = model.predict(preprocessed_tweets_trump)
biden_predictions = model.predict(preprocessed_tweets_biden)

# Convert probabilities to class labels
predicted_classes_trump = trump_predictions.argmax(axis=-1)
predicted_classes_biden = biden_predictions.argmax(axis=-1)

# Map numeric classes to sentiment labels
class_mapping = {0: "Negative", 1: "Neutral", 2: "Positive"}
predicted_labels_trump = [class_mapping[label] for label in predicted_classes_trump]
predicted_labels_biden = [class_mapping[label] for label in predicted_classes_biden]

# Print the results
# trump tweets
for i, label in enumerate(predicted_labels_trump):
    row = trumpdata.iloc[i].to_dict()
    if label == 'Positive':
        positive_trump.append(row)
    elif label == 'Negative':
        negative_trump.append(row)
    elif label == 'Neutral':
        neutral_trump.append(row)

# biden tweets
for i, label in enumerate(predicted_labels_biden):
    row = bidendata.iloc[i].to_dict()
    if label == 'Positive':
        positive_biden.append(row)
    elif label == 'Negative':
        negative_biden.append(row)
    elif label == 'Neutral':
        neutral_biden.append(row)

NameError: name 'model' is not defined

In [3]:
# demo show the results in percentage
count_positive_trump = len(positive_trump) / len(trumpdata) * 100
count_negative_trump = len(negative_trump) / len(trumpdata) * 100
count_neutral_trump = len(neutral_trump) / len(trumpdata) * 100

count_positive_biden = len(positive_biden) / len(bidendata) * 100
count_negative_biden = len(negative_biden) / len(bidendata) * 100
count_neutral_biden = len(neutral_biden) / len(bidendata) * 100

print('Trump')
print('Positive:', count_positive_trump, '%')
print('Negative:', count_negative_trump, '%')
print('Neutral:', count_neutral_trump, '%')

print('Biden')
print('Positive:', count_positive_biden, '%')
print('Negative:', count_negative_biden, '%')
print('Neutral:', count_neutral_biden, '%')

# Plot the results using 
sns.set_style("whitegrid")
plt.figure(figsize=(10, 6))
sns.barplot(x=['Positive', 'Negative', 'Neutral'], y=[count_positive_trump, count_negative_trump, count_neutral_trump])
plt.title("Sentiment Analysis of Trump's Tweets")
plt.ylabel("Percentage")
plt.show()

plt.figure(figsize=(10, 6))
sns.barplot(x=['Positive', 'Negative', 'Neutral'], y=[count_positive_biden, count_negative_biden, count_neutral_biden])
plt.title("Sentiment Analysis of Biden's Tweets")
plt.ylabel("Percentage")
plt.show()


NameError: name 'positive_trump' is not defined

In [ ]:
# demo: show negative biden tweets
for tweet_data in negative_biden:
    if isinstance(tweet_data, dict):
        print(tweet_data['tweet'])
        print('state:', tweet_data['state'])
        print('---')

in 2020 nypost is being censorship censored by twitter to manipulate a us election in favor of joebiden and against trump

but ccp from china or porn on twitter 

that’s always been fine for jack vijaya dickc katies

marciadorsey is jack sick
state: Illinois
---
fbi allegedly obtained hunter biden computer data on ukraine dealings report claims joebiden hunterbiden httpstcopdnmb0nqru
state: Kentucky
---
comments on this do democrats understand how ruthless china is httpstcoqevk00yhs3 china hunterbiden joebiden bidenharris bidenharris2020 trumppence2020 trump realdonaldtrump wto coronavirus trade httpstcowjm1hytfnz
state: Florida
---
has this awoken you from your slumbers yet bbcjonsopel getting to the point where even you may have to file a negative story about biden httpstcoy54y25n6du
state: Virginia
---
hunter biden introduced his father thenvice president joe biden to a top executive at a ukrainian energy firm less than a year before the elder biden pressured government officials in